### Define key loading and plotting functions

In [1]:
import dash
import plotly.express as px
from ome_zarr.io import parse_url
from ome_zarr.reader import Reader
import plotly.graph_objs as go
import pandas as pd
import numpy as np
import json
import glob2 as glob
from skimage.measure import regionprops
import itertools
import os
from scipy.interpolate import LinearNDInterpolator
import alphashape


def load_nucleus_dataset(filename):
    # global fin_points_prev, not_fin_points_prev, class_predictions_curr, df, curationPath, propPath

    propPath = dataRoot + filename + '_nucleus_props.csv'

    if os.path.isfile(propPath):
        df = pd.read_csv(propPath, index_col=0)
    else:
        raise Exception(
            f"Selected dataset( {filename} ) dataset has no nucleus data. Have you run extract_nucleus_stats?")

#     fin_nuclei = np.where(df["pec_fin_flag"] == 1)
#     df = df.iloc[fin_nuclei]

    # normalize gene expression levels
    colnames = df.columns
    list_raw = [item for item in colnames if "_cell_mean_nn" in item]
    gene_names = [item.replace("_cell_mean_nn", "") for item in list_raw]

    for g in gene_names:
        ind_list = [i for i in range(len(colnames)) if g in colnames[i]]
        for ind in ind_list:
            colname = colnames[ind]
            c_max = np.max(df[colname])
            df[colname] = df.loc[:, colname] / c_max

    return df





/Users/nick/miniforge3/envs/napari-env/lib/python3.10/site-packages/geopandas/_compat.py:106: UserWarning: The Shapely GEOS version (3.11.1-CAPI-1.17.1) is incompatible with the GEOS version PyGEOS was compiled with (3.10.4-CAPI-1.16.2). Conversions between both will be slow.
  warnings.warn(


## Get list of files

In [2]:
dataRoot = "/Users/nick/Dropbox (Cole Trapnell's Lab)/Nick/pecFin/HCR_Data/nucleus_props/"
figureRoot = "/Users/nick/Dropbox (Cole Trapnell's Lab)/Nick/pecFin/HCR_figures/"
if os.path.isdir(figureRoot) == False:
    os.makedirs(figureRoot)
    
# get list of filepaths
fileList = sorted(glob.glob(dataRoot + '*_nucleus_props.csv'))
pdNameList = []
for fn in range(len(fileList)):
    labelName = fileList[fn].replace(dataRoot, '', 1)
    labelName = labelName.replace('_nucleus_props.csv', '')
    pdNameList.append(labelName)

# compile dictionary of gene names that correspond to each dataset
gene_name_dict = {}
for f in range(len(fileList)):
    filename_temp = pdNameList[f]
    propPath = dataRoot + filename_temp + '_nucleus_props.csv'

    if os.path.isfile(propPath):
        df_temp = pd.read_csv(propPath, index_col=0)
    else:
        raise Exception(
            f"Selected dataset( {filename_temp} ) dataset has no nucleus data. Have you run extract_nucleus_stats?")

    # get list of genes that we can look at
    colnames_temp = df_temp.columns
    list_raw = [item for item in colnames_temp if "_cell_mean_nn" in item]
    gene_names_temp = [item.replace("_cell_mean_nn", "") for item in list_raw]

    gene_name_dict[filename_temp] = gene_names_temp

## Test that plotting is working

In [75]:
import math 
import shutil

df_ind = 2

fileName = fileList[df_ind]
imageName = pdNameList[df_ind]
plot_type = "Volume Plot"
# gene_name = gene_name_dict[imageName][df_ind]

df = load_nucleus_dataset(imageName)
df_fin = df.iloc[np.where(df["pec_fin_flag"]==2)]


################
# basic nucleus position plot

r_vec = np.sqrt(df["X"].to_numpy()**2 + df["Y"].to_numpy()**2 + df["Z"].to_numpy()**2)

# make save directory
frame_dir = figureRoot + imageName + "_raw_nucleus_frames/"
if os.path.isdir(frame_dir)==True:
    shutil.rmtree(frame_dir)

os.makedirs(frame_dir)

angle_vec_raw = np.linspace(1.25*np.pi, 3.25*np.pi, 25)
angle_vec_flipped = angle_vec_raw[::-1]
angle_vec = np.concatenate([angle_vec_raw, angle_vec_flipped[:-1]])

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))

    fig = px.scatter_3d(df, x="X", y="Y", z="Z", opacity=0.5, color=r_vec, 
                        color_continuous_scale="ice",template="plotly_white")
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene = dict(
                    xaxis_title='',
                    yaxis_title='',
                    zaxis_title='',
                    xaxis = dict(showticklabels=False),
                    yaxis = dict(showticklabels=False),
                    zaxis = dict(showticklabels=False)))
    
    fig.update_layout(coloraxis_showscale=False)
    
#     fig.show()
    fig.write_image(frame_dir + imageName + "_" + "{:03d}".format(iter_i) + ".png")
#     time.sleep(0.25)

In [ ]:
import plotly.express as px
import math 

angle_vec_raw = np.linspace(1.25*np.pi, 3.25*np.pi, 25) # vector defining range of different views
angle_vec_flipped = angle_vec_raw[::-1]
angle_vec = np.concatenate([angle_vec_raw, angle_vec_flipped[:-1]]) # for mine, I added a full reverse rotation. You might not want this

for iter_i, angle in enumerate(angle_vec):

    za = 0.3 # sets z elevation of view
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2 # sets overall zoom 
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))

    fig = px.scatter_3d(df, x="X", y="Y", z="Z", opacity=0.5, color=r_vec, 
                        color_continuous_scale="ice",template="plotly_white")
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit') # I'm not sure if the second argument here does anything

    fig.write_image(folder_path + image_name + "_" + "{:03d}".format(iter_i) + ".png")

## Make basic plots illustrating fin segmentation

In [ ]:
fin_indices = np.where(df["pec_fin_flag"]==2)
not_fin_indices = np.where(df["pec_fin_flag"]!=2)

scene_dict = dict(
            xaxis_title='',
            yaxis_title='',
            zaxis_title='',
            xaxis = dict(showticklabels=False),
            yaxis = dict(showticklabels=False),
            zaxis = dict(showticklabels=False))

# make save directory
seg_dir = figureRoot + imageName + "/fin_segmentation/"
if os.path.isdir(seg_dir)==True:
    shutil.rmtree(seg_dir)

os.makedirs(seg_dir)

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))

    fig = px.scatter_3d(df.iloc[not_fin_indices], x="X", y="Y", z="Z", opacity=0.3, color=r_vec[not_fin_indices], 
                        color_continuous_scale="ice", template="plotly_white")
    
    fig.add_trace(go.Scatter3d(x=df["X"].iloc[fin_indices], 
                               y=df["Y"].iloc[fin_indices],
                               z=df["Z"].iloc[fin_indices],
                               mode='markers',
                               marker=dict(opacity=0.4, color=r_vec[fin_indices],
                                          colorscale="greens")))
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
    fig.write_image(seg_dir + imageName + "_" + "{:03d}".format(iter_i) + ".png")

### Surface fitting

In [77]:
# Import the necessaries libraries
import plotly.offline as pyo
import plotly.graph_objs as go
from sklearn.decomposition import PCA
from sklearn.neighbors import KDTree
import open3d as o3d 
import pickle
import alphashape
import scipy

# fit sphere to base
fin_indices = np.where(df["pec_fin_flag"]==2)
not_fin_indices = np.where(df["pec_fin_flag"]!=2)

def sphereFit_fixed_r(spX, spY, spZ, r0):
    #   Assemble the A matrix
    spX = np.array(spX)
    spY = np.array(spY)
    spZ = np.array(spZ)

    xyz_array = np.zeros((len(spX), 3))
    xyz_array[:, 0] = spX
    xyz_array[:, 1] = spY
    xyz_array[:, 2] = spZ
    c0 = np.mean(xyz_array, axis=0)
    c0[2] = -r0

    def ob_fun(c0, xyz=xyz_array, r=r0):
        res = np.sqrt((xyz[:, 0] - c0[0]) ** 2 + (xyz[:, 1] - c0[1]) ** 2 + (xyz[:, 2] - c0[2]) ** 2) - r
        return res

    C = scipy.optimize.least_squares(ob_fun, c0, bounds=([-np.inf, -np.inf, -np.inf], [np.inf, np.inf, 0]))

    return r0, C.x[0], C.x[1], C.x[2]


base_nuclei = np.where(df["pec_fin_flag"] == 1)[0]
xyz_base = df[["X", "Y", "Z"]].iloc[base_nuclei]
xyz_base = xyz_base.to_numpy()
# print(xyz_base)
r, x0, y0, z0 = sphereFit_fixed_r(xyz_base[:, 0], xyz_base[:, 1], xyz_base[:, 2], 250)
c0 = [x0, y0, z0]


# Set notebook mode to work in offline
pyo.init_notebook_mode()

k_nn = 7

#################
# load surface model and pca info
curation_path = dataRoot + imageName +  "_curation_info/"

with open(curation_path + "fin_surf_model.pkl", 'rb') as fn:
    fin_surf = pickle.load(fn)
surface_model = np.asarray(json.loads(fin_surf))

with open(curation_path + "pca_fin.pkl", 'rb') as fn:
    pca_components = pickle.load(fn)
pca_components = np.asarray(json.loads(pca_components))


###################
# Transform fin nuclei to PCA space
xyz_array = df[["X", "Y", "Z"]].to_numpy()
tree = KDTree(xyz_array)
nearest_dist, nearest_ind = tree.query(xyz_array, k=k_nn + 1)

# find average distance to kth closest neighbor
mean_nn_dist_vec = np.mean(nearest_dist, axis=0)
nn_thresh = mean_nn_dist_vec[k_nn]
nn_thresh_small = mean_nn_dist_vec[1]
    
xyz_fin = df[["X", "Y", "Z"]].iloc[fin_indices].to_numpy()

dist_array = np.sqrt(np.sum((c0 - xyz_fin) ** 2, axis=1)) - r
surf_indices = np.where(dist_array <= nn_thresh)[0]
xyz_surf = xyz_fin[surf_indices]

# calculate centroid
surf_cm = np.mean(xyz_surf, axis=0)

# calculate PCA
pca_surf = PCA(n_components=3)

pca_surf.fit(xyz_surf)
vec1 = pca_surf.components_[0]
vec2 = surf_cm - c0
vec2 = vec2 / np.sqrt(np.sum(vec2 ** 2))
plane_normal = np.cross(vec1, vec2)
plane_normal_u = plane_normal / np.sqrt(np.sum(plane_normal ** 2))
D_plane = -np.dot(plane_normal, surf_cm)

# generate additional points to constrain the axis fit such that it is approximately normal to the sphere when
# it intersects the sphere surface
# In future, we could consider adding a constraint directly to the objective function that enforces this
c_vec = surf_cm - c0
c_vec_u = c_vec / np.sqrt(np.sum(c_vec ** 2))
lower_point = surf_cm - 2*c_vec_u*nn_thresh_small
n_reps = 6
add_array = np.empty((n_reps*n_reps+1, 3))
add_array[0, :] = lower_point
for n in range(n_reps):
    ind = 2*n
    add_array[ind+1, :] = lower_point + nn_thresh*vec1*(n+1)
    add_array[ind+2:, :] = lower_point - nn_thresh*vec1*(n+1)

#######################
# fit surface to fin points
#######################
xyz_fin_raw = df[["X", "Y", "Z"]].iloc[fin_indices]
xyz_surf = xyz_fin_raw.iloc[surf_indices].to_numpy()

# exclude base points that are too far from our plane prior. If included, these will tend to cause the
# surface fit to perform poorly
d_surf = np.abs(np.sum(np.multiply(plane_normal_u, xyz_surf), axis=1) + D_plane)
ind_rm = surf_indices[np.where(d_surf > nn_thresh)[0]]
keep_indices = [k for k in range(xyz_fin_raw.shape[0]) if k not in ind_rm]
xyz_fin = xyz_fin_raw.iloc[keep_indices].copy()

# convert to point cloud and downsample points
tree = KDTree(xyz_fin.to_numpy())
nearest_dist, nearest_ind = tree.query(xyz_fin.to_numpy(), k=2)

# find average distance to kth closest neighbor
mean_nn_dist_vec = np.mean(nearest_dist, axis=0)
nn_thresh1 = mean_nn_dist_vec[1] # sets scale for downsampling withing the fin

# downsample to achieve uniform distribution of fit points
pcd = o3d.geometry.PointCloud()
pcd.points = o3d.utility.Vector3dVector(xyz_fin.to_numpy())
pcd_down = pcd.voxel_down_sample(voxel_size=nn_thresh1 * 1.5)
xyz_fin_down = np.asarray(pcd_down.points)

# Transform to PCA space
PCAFIN = PCA(n_components=3)
PCAFIN.fit(xyz_fin_down)

##########
# pca_fin = PCAFIN.transform(xyz_fin.to_numpy())
pca_fin = PCAFIN.transform(xyz_fin_raw.to_numpy())

# #################
# obtain surface prediction
grid_res = 100
P0, P1 = np.meshgrid(np.linspace(np.min(pca_fin[:, 0]), np.max(pca_fin[:, 0]), grid_res),
                     np.linspace(np.min(pca_fin[:, 1]), np.max(pca_fin[:, 1]), grid_res))

PP0 = P0.flatten()
PP1 = P1.flatten()

P2_curve = np.dot(np.c_[np.ones(PP0.shape), PP0, PP1, PP0 * PP1, PP0 ** 2, PP1 ** 2], surface_model).reshape(P0.shape)


####################
# Transform back to xyz space
xyz_fit_curve = PCAFIN.inverse_transform(np.concatenate((np.reshape(P0, (P0.size, 1)),
                                                         np.reshape(P1, (P1.size, 1)),
                                                         np.reshape(P2_curve, (P2_curve.size, 1))),
                                                         axis=1))
                                         
# make plots
XS = np.reshape(xyz_fit_curve[:, 0], (P0.shape))
YS = np.reshape(xyz_fit_curve[:, 1], (P0.shape))
ZS = np.reshape(xyz_fit_curve[:, 2], (P0.shape))

xyz_fit_curve_norm = xyz_fit_curve / np.max(xyz_fin_raw.to_numpy(), axis=0)
xyz_plot = xyz_fin_raw.to_numpy()
xyz_fin_norm = xyz_fin_raw.to_numpy() / np.max(xyz_fin_raw.to_numpy(), axis=0)
alphafin = alphashape.alphashape(xyz_fin_norm, 0.1)
inside_flags = np.reshape(alphafin.contains(xyz_fit_curve_norm), (grid_res, grid_res))

ZS[np.where(inside_flags!=1)] = np.nan

### Make surface plot

In [118]:
# plot just the fin
just_fin_dir = figureRoot + imageName + "/fin_only/"
if os.path.isdir(just_fin_dir)==True:
    shutil.rmtree(just_fin_dir)

os.makedirs(just_fin_dir)

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
    fig = go.Figure()
    
    fig.add_trace(go.Scatter3d(x=xyz_plot[:, 0], y=xyz_plot[:, 1], z=xyz_plot[:, 2],
                           mode='markers',
                           marker=dict(opacity=0.65, color=r_vec[fin_indices], colorscale="Greys")))
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
    fig.write_image(just_fin_dir + imageName + "_" + "{:03d}".format(iter_i) + ".png")
    


# fig = go.Figure()

# # px.scatter_3d(x=xyz_plot[:, 0], y=xyz_plot[:, 1], z=xyz_plot[:, 2], 
# #                     opacity=0.25, color=r_vec[fin_indices], 
# #                     template="plotly_white",
# #                     color_continuous_scale="Greens")

# fig.add_trace(go.Surface(x=XS, y=YS, z=ZS, opacity=0.75, showscale=False))
# fig.add_trace(go.Scatter3d(x=xyz_plot[:, 0], y=xyz_plot[:, 1], z=xyz_plot[:, 2],
#                            mode='markers',
#                            marker=dict(opacity=0.25, color=r_vec[fin_indices], colorscale="Greys")))

# fig.add_trace(go.Surface(x=XS, y=YS, z=ZS, opacity=0.2, showscale=False))
# fig.show()

In [119]:
# plot fin with surface
fin_surf_dir = figureRoot + imageName + "/fin_surf/"
if os.path.isdir(fin_surf_dir)==True:
    shutil.rmtree(fin_surf_dir)

os.makedirs(fin_surf_dir)

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
    fig = go.Figure()
    
    fig.add_trace(go.Surface(x=XS, y=YS, z=ZS, opacity=0.75, showscale=False))
    
    fig.add_trace(go.Scatter3d(x=xyz_plot[:, 0], y=xyz_plot[:, 1], z=xyz_plot[:, 2],
                           mode='markers',
                           marker=dict(opacity=0.35, color=r_vec[fin_indices], colorscale="Greys")))
    
    fig.add_trace(go.Surface(x=XS, y=YS, z=ZS, opacity=0.2, showscale=False))
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
    fig.write_image(fin_surf_dir + imageName + "_" + "{:03d}".format(iter_i) + ".png")

## Illustrate surface point mapping proces

In [123]:
import random

np.random.seed(127)

n_plot = 25
# dv_filter = np.where(df["DV_pos"]<=30)[0]
surf_indices = np.where(~np.isnan(df["Z_PD_st"]))[0]
# surf_indices = [s for s in surf_indices if s in dv_filter]
plot_indices = np.random.choice(surf_indices, size=n_plot, replace=False)


# surf_points1 = figureRoot + imageName + "/surf_points1/"
# if os.path.isdir(surf_points1)==True:
#     shutil.rmtree(surf_points1)

# os.makedirs(surf_points1)

for iter_i, a in enumerate([angle_vec[0]]):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
    fig = go.Figure()

    fig.add_trace(go.Surface(x=XS, y=YS, z=ZS, opacity=0.7, showscale=False))

    fig.add_trace(go.Mesh3d(x=df["X"].iloc[fin_indices], 
                             y=df["Y"].iloc[fin_indices], 
                             z=df["Z"].iloc[fin_indices], opacity=0.25, alphahull=9,color="gray"))
    
    fig.add_trace(go.Scatter3d(x=xyz_plot[:, 0], y=xyz_plot[:, 1], z=xyz_plot[:, 2],
                               mode='markers',
                               marker=dict(opacity=0.01, color=r_vec[fin_indices], colorscale="Greys"),
                               line=dict(width=1,
                                         color='DarkSlateGrey'))
                 )


    fig.add_trace(go.Mesh3d(x=XS, y=YS, z=ZS,
                                    alphahull=9,
                                    opacity=0.2,
                                    color='gray'))
    
    for p in plot_indices:
        xyz0 = df[["X", "Y", "Z"]].iloc[p].to_numpy()
        xyz1 = df[["X_surf", "Y_surf", "Z_surf"]].iloc[p].to_numpy()
        fig.add_trace(go.Scatter3d(x=[xyz0[0], xyz1[0]], y=[xyz0[1], xyz1[1]], z=[xyz0[2], xyz1[2]]))
        
    fig.update_layout(showlegend=False)
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
    fig.show()
    
#     fig.write_image(surf_points1 + imageName + "_" + "{:03d}".format(iter_i) + ".png")
    


In [110]:
surf_points2 = figureRoot + imageName + "/surf_points2/"
if os.path.isdir(surf_points2)==True:
    shutil.rmtree(surf_points2)

os.makedirs(surf_points2)

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
    fig = go.Figure()


    fig.add_trace(go.Surface(x=XS, y=YS, z=ZS, opacity=0.75, showscale=False))
#     fig.add_trace(go.Scatter3d(x=xyz_plot[:, 0], y=xyz_plot[:, 1], z=xyz_plot[:, 2],
#                                mode='markers',
#                                marker=dict(opacity=0.15, color=r_vec[fin_indices], colorscale="Greys")))

    fig.add_trace(go.Surface(x=XS, y=YS, z=ZS, opacity=0.2, showscale=False))
    
    for p in plot_indices:
        xyz0 = df[["X", "Y", "Z"]].iloc[p].to_numpy()
        xyz1 = df[["X_surf", "Y_surf", "Z_surf"]].iloc[p].to_numpy()
        fig.add_trace(go.Scatter3d(x=[xyz0[0], xyz1[0]], y=[xyz0[1], xyz1[1]], z=[xyz0[2], xyz1[2]]))
        
    fig.update_layout(showlegend=False)
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
    fig.write_image(surf_points2 + imageName + "_" + "{:03d}".format(iter_i) + ".png")

### Illustrate unfolding

In [113]:
curved_surf = figureRoot + imageName + "/curved_surf/"
if os.path.isdir(curved_surf)==True:
    shutil.rmtree(curved_surf)

os.makedirs(curved_surf)

plot_indices_all = np.random.choice(surf_indices, size=len(surf_indices), replace=False)

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
    fig = go.Figure()
    
    for p in plot_indices_all:
        xyz0 = df[["X", "Y", "Z"]].iloc[p].to_numpy()
        xyz1 = df[["X_surf", "Y_surf", "Z_surf"]].iloc[p].to_numpy()
        fig.add_trace(go.Scatter3d(x=[xyz1[0]], y=[xyz1[1]], z=[xyz1[2]], mode='markers',
                                   marker=dict(opacity=1)))
        
    fig.update_layout(showlegend=False)
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
    fig.write_image(curved_surf + imageName + "_" + "{:03d}".format(iter_i) + ".png")
    
    
# # curved surface
# fig = px.scatter_3d(df.iloc[surf_indices], x="X_surf", y="Y_surf", z="Z_surf", opacity=0.5, color="Z_PD_st")
# fig.show()

# # straightened surface
# fig = px.scatter_3d(df.iloc[surf_indices], x="X_AP_st", y=np.ones((len(surf_indices),)), z="Z_PD_st", 
#                     opacity=0.5, color="Z_PD_st")
# fig.show()

In [115]:
straight_surf = figureRoot + imageName + "/straight_surf/"
if os.path.isdir(straight_surf)==True:
    shutil.rmtree(straight_surf)

os.makedirs(straight_surf)

plot_indices_all = np.random.choice(surf_indices, size=len(surf_indices), replace=False)

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
    fig = go.Figure()
    
    for p in plot_indices_all:
        xyz0 = df[["X_AP_st", "Y_DV_st", "Z_PD_st"]].iloc[p].to_numpy()
        fig.add_trace(go.Scatter3d(x=[xyz0[0]], y=np.ones((len(surf_indices),)), z=[xyz0[2]], mode='markers',
                                   marker=dict(opacity=1)))
        
    fig.update_layout(showlegend=False)
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
    fig.write_image(straight_surf + imageName + "_" + "{:03d}".format(iter_i) + ".png")

## Show reverse point projection

In [137]:
np.random.seed(127)


straight_points = figureRoot + imageName + "/straight_points2/"
if os.path.isdir(straight_points)==True:
    shutil.rmtree(straight_points)

os.makedirs(straight_points)

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
    fig = go.Figure()

    for p in plot_indices_all:
        xyz0 = df[["X_AP_st", "Y_DV_st", "Z_PD_st"]].iloc[p].to_numpy()
        fig.add_trace(go.Scatter3d(x=[xyz0[0]], y=np.ones((len(surf_indices),)), z=[xyz0[2]], mode='markers',
                                   marker=dict(opacity=0.5)))
        
    for p in plot_indices:
        xyz0 = df[["X_AP_st", "Y_DV_st", "Z_PD_st"]].iloc[p].to_numpy()
#         xyz1 = df[["X_surf", "Y_surf", "Z_surf"]].iloc[p].to_numpy()
#         if p not in plot_indices:
#             fig.add_trace(go.Scatter3d(x=[xyz0[0]], y=np.ones((len(surf_indices),)), z=[xyz0[2]], mode='markers',
#                                        marker=dict(opacity=0.15)))

#         else:
        xyz1 = xyz0.copy()
        xyz1[1] = 1
        fig.add_trace(go.Scatter3d(x=[xyz0[0], xyz1[0]], y=[xyz0[1], xyz1[1]], z=[xyz0[2], xyz1[2]]))

#     fig.add_trace(go.Mesh3d(x=df["X_AP_st"].iloc[surf_indices], 
#                              y=df["Y_DV_st"].iloc[surf_indices], 
#                              z=df["Z_PD_st"].iloc[surf_indices], opacity=0.25, alphahull=5, color="gray"))

    fig.update_layout(showlegend=False)
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
#     fig.show()
    
    fig.write_image(straight_points + imageName + "_" + "{:03d}".format(iter_i) + ".png")

### Finally, plot full "streightened" fin

In [135]:
straight_fin = figureRoot + imageName + "/straightened_fin_pd/"
if os.path.isdir(straight_fin)==True:
    shutil.rmtree(straight_fin)

os.makedirs(straight_fin)

plot_indices_all = np.random.choice(surf_indices, size=len(surf_indices), replace=False)

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
    fig = go.Figure()
    
    fig.add_trace(go.Scatter3d(x=df["X_AP_st"].iloc[surf_indices], 
                               y=df["Y_DV_st"].iloc[surf_indices],
                               z=df["Z_PD_st"].iloc[surf_indices],
                               mode='markers',
                               marker=dict(color=df["Z_PD_st"].iloc[surf_indices],
                                           opacity=0.5)))

    fig.update_layout(showlegend=False)
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
    fig.write_image(straight_fin + imageName + "_" + "{:03d}".format(iter_i) + ".png")

In [ ]:
straight_fin_ap = figureRoot + imageName + "/straightened_fin_ap/"
if os.path.isdir(straight_fin_ap)==True:
    shutil.rmtree(straight_fin_ap)

os.makedirs(straight_fin_ap)

plot_indices_all = np.random.choice(surf_indices, size=len(surf_indices), replace=False)

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
    fig = go.Figure()
    
    fig.add_trace(go.Scatter3d(x=df["X_AP_st"].iloc[surf_indices], 
                               y=df["Y_DV_st"].iloc[surf_indices],
                               z=df["Z_PD_st"].iloc[surf_indices],
                               mode='markers',
                               marker=dict(color=df["X_AP_st"].iloc[surf_indices],
                                           colorscale="PiYG",
                                           opacity=0.5)))

    fig.update_layout(showlegend=False)
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
    fig.write_image(straight_fin_ap + imageName + "_" + "{:03d}".format(iter_i) + ".png")

In [ ]:
straight_fin_dv = figureRoot + imageName + "/straightened_fin_dv/"
if os.path.isdir(straight_fin_dv)==True:
    shutil.rmtree(straight_fin_dv)

os.makedirs(straight_fin_dv)

for iter_i, a in enumerate(angle_vec):
    angle = a
    za = 0.3
    vec = np.asarray([math.cos(angle), math.sin(angle), za])
    vec = vec*2
    camera = dict(
        eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
    fig = go.Figure()
    
    fig.add_trace(go.Scatter3d(x=df["X_AP_st"].iloc[surf_indices], 
                               y=df["Y_DV_st"].iloc[surf_indices],
                               z=df["Z_PD_st"].iloc[surf_indices],
                               mode='markers',
                               marker=dict(color=df["Y_DV_st"].iloc[surf_indices],
                                           colorscale="Geyser",
                                           opacity=0.5)))

    fig.update_layout(showlegend=False)
    
    fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    
    fig.update_layout(scene=scene_dict)
    
    fig.update_layout(coloraxis_showscale=False)
    
    fig.write_image(straight_fin_dv + imageName + "_" + "{:03d}".format(iter_i) + ".png")

In [ ]:
# import cv2
# import os

# image_folder = 'images'
# video_name = 'video.avi'

# images = [img for img in os.listdir(subdir) if img.endswith(".png")]
# frame = cv2.imread(os.path.join(image_folder, images[0]))
# height, width, layers = frame.shape

# video = cv2.VideoWriter(video_name, 0, 1, (width,height))

# for image in images:
#     video.write(cv2.imread(os.path.join(image_folder, image)))

# cv2.destroyAllWindows()
# video.release()

## Use sphere fit to correct PD position

In [ ]:
import scipy 

def sphereFit_fixed_r(spX,spY,spZ,r0):
    
    #   Assemble the A matrix
    spX = np.array(spX)
    spY = np.array(spY)
    spZ = np.array(spZ)

    xyz_array = np.zeros((len(spX), 3))
    xyz_array[:, 0] = spX
    xyz_array[:, 1] = spY
    xyz_array[:, 2] = spZ
    c0 = np.mean(xyz_array, axis=0)
    c0[2] = -r0
    def ob_fun(c0, xyz=xyz_array, r=r0):
        res = np.sqrt((xyz[:, 0]-c0[0])**2 + (xyz[:, 1]-c0[1])**2 + (xyz[:, 2]-c0[2])**2) - r
        return res

    C = scipy.optimize.least_squares(ob_fun, c0, bounds=([-np.inf, -np.inf, -np.inf], [np.inf, np.inf, 0]))

    return r0, C.x[0], C.x[1], C.x[2]


# fit the function
base_nuclei = np.where(df["pec_fin_flag"]==1)[0]
xyz_base = df[["X", "Y", "Z"]].iloc[base_nuclei]
xyz_base = xyz_base.to_numpy()
# print(xyz_base)
r, x0, y0, z0 = sphereFit_fixed_r(xyz_base[:, 0], xyz_base[:, 1], xyz_base[:, 2], 250)
c0 = [x0, y0, z0]


# get indices of fin nuclei
fin_indices = np.where(df["pec_fin_flag"]==2)[0]
df_fin = df.iloc[fin_indices]
dv_filter = np.where(np.abs(df_fin["DV_pos"]) <= 30)
df_fin = df_fin.iloc[dv_filter]

pd_vec = df_fin["PD_pos"].to_numpy()

surf_array = df_fin[["X_surf", "Y_surf", "Z_surf"]].to_numpy()
dist_array = np.sqrt(np.sum((c0 - surf_array)**2, axis=1))
outside_indices = np.where(dist_array>=r)[0]
inside_indices = np.where(dist_array<r)[0]
pd_vec[outside_indices] = np.abs(pd_vec[outside_indices])
pd_vec[inside_indices] = -np.abs(pd_vec[inside_indices])

# assign to dataframe
df_fin["PD_pos"] = pd_vec

In [ ]:

# make basic scatter plot
fig = px.scatter_3d(df_fin, x="X", y="Y", z="Z", color="PD_pos", template="plotly_white", opacity=0.25)
fig.show()

# make basic scatter plot
fig = px.scatter_3d(df_fin, x="X_AP_st", y="Y_DV_st", z="Z_PD_st", color="PD_pos", template="plotly_white", opacity=0.25)
fig.show()





## Let's try nonlinear DMR instead

In [ ]:
from sklearn.manifold import Isomap

# dirst plot the surface projections of each point
fig = px.scatter_3d(df_fin, x="X_surf", y="Y_surf", z="Z_surf", color="PD_pos", template="plotly_white", opacity=0.5)
fig.show()

# try unfolding 
surf_array = df_fin[["X_surf", "Y_surf", "Z_surf"]].to_numpy()
embedding = Isomap(n_components=2)
surf_transformed = embedding.fit_transform(surf_array)

fig = px.scatter_3d(x=surf_transformed[:, 0], y=np.zeros((surf_transformed[:, 0].size,)), 
                    z=surf_transformed[:, 1], color=df_fin["PD_pos"], template="plotly_white", opacity=0.5)
fig.show()


### We need to rotate the transformed axes to align with PD and AP directions

In [ ]:
from sklearn.linear_model import LinearRegression

# use linear regression to back out correspondence between PD axis and the isomap dimensions
reg = LinearRegression().fit(surf_transformed, pd_vec)

new_axis1 = reg.coef_
new_axis1 = new_axis1 / np.sqrt(np.sum((new_axis1**2)))
new_axis2 = [-new_axis1[1], new_axis1[0]]

surf_tr_new = np.empty((surf_transformed.shape))
surf_tr_new[:, 0] = new_axis1[0]*surf_transformed[:, 0] + new_axis1[1]*surf_transformed[:, 1]
surf_tr_new[:, 1] = new_axis2[0]*surf_transformed[:, 0] + new_axis2[1]*surf_transformed[:, 1]

fig = px.scatter_3d(x=surf_tr_new[:, 1], y=np.zeros((surf_transformed[:, 0].size,)), 
                    z=surf_tr_new[:, 0], color=df_fin["PD_pos"], template="plotly_white", opacity=0.5)
fig.show()


fig = px.scatter_3d(x=surf_tr_new[:, 1], y=df_fin["DV_pos"], 
                    z=surf_tr_new[:, 0], color=df_fin["PD_pos"], template="plotly_white", opacity=0.5)
fig.show()


In [ ]:
print(reg.coef_)

In [ ]:
# normalize AP and PD axes
surf_transformed_norm = surf_tr_new-np.min(surf_tr_new, axis=0)

# # make it so that we are measuring PD position relative to tip of fin
# surf_transformed_norm[:, 0] = np.max(surf_transformed_norm[:, 0]) - surf_transformed_norm[:, 0]
# surf_transformed_norm = np.divide(surf_transformed, np.max(surf_transformed, axis=0))

# center the AP coordinates
surf_transformed_norm[:, 1] = surf_transformed_norm[:, 1] - np.mean(surf_transformed_norm[:, 1], axis=0)

# add dv info
dv_array = np.reshape(df_fin["DV_pos"].to_numpy(), (df_fin.shape[0], 1))
# dv_array = dv_array / np.max(np.abs(dv_array))

new_coord_array = np.concatenate((surf_transformed_norm, dv_array), axis=1)

fig = px.scatter_3d(x=new_coord_array[:, 1], y=new_coord_array[:, 2], 
                    z=new_coord_array[:, 0], color=new_coord_array[:, 1], template="plotly_white", opacity=0.5)

# fig.update_layout(
#             scene=dict(
#                 aspectratio=dict(x=1, y=0.2, z=1)))
fig.show()



In [ ]:
from matplotlib.animation import FuncAnimation
import matplotlib.pyplot as plt
from IPython.display import HTML
import numpy as np
from scipy.stats import gamma, poisson

np.random.seed(0)

fig, ax = plt.subplots()
line, = ax.plot([], [])

def animate(i):
    if i == 0:
        x = np.linspace(0, 30, 1000)
        alpha = 2
        beta = 1
        y = gamma.pdf(x, a=alpha, scale=beta)
        line.set_data(x, y)
        return line,
    else:
        x = np.linspace(0, 30, 1000)
        alpha = 2
        beta = 1
        sample = poisson.rvs(4)
        alpha += sample
        beta += 1
        y = gamma.pdf(x, a=alpha, scale=beta)
        line.set_data(x, y)
        return line,

anim = FuncAnimation(fig, animate, frames=2, blit=True)
# plt.show()

plt.close()
HTML(anim.to_html5_video())

## Record spinning fin plots

In [ ]:
# experiment with for loop that rotates fin about z axis
import plotly.graph_objects as go
import  moviepy.editor as mpy
import io 
from PIL import Image

if 'f' in globals():
    del f
    
    
plot_type = "Volume Plot"
imageName = imNameList[0]
df = load_nucleus_dataset(imageName)
for g in range(0,2):
    gene_name = gene_name_dict[imageName][g]

    outDir = "/Users/nick/Dropbox (Cole Trapnell's Lab)/Nick/pecFin/HCR_Data/figures/dynamic_plots/"
    if not os.path.isdir(outDir):
        os.makedirs(outDir)

    fig = create_figure(df, gene_name=gene_name, plot_type=plot_type)

    fig.update_layout(template="plotly_white")

    def plotly_fig2array(fig):
        #convert Plotly fig to  an array
        fig_bytes = fig.to_image(format="png")
        buf = io.BytesIO(fig_bytes)
        img = Image.open(buf)
        return np.asarray(img)


    t = np.linspace(0, 40*np.pi, 10)
    x, y, z = np.cos(t), np.sin(t), t

    x_eye = -1.25
    y_eye = 2
    z_eye = 0.5

    fig.update_layout(title_text=gene_name,
                      scene_camera_eye=dict(x=x_eye, y=y_eye, z=z_eye),
                      width=500, height=500, 
                      scene_xaxis_visible=False, 
                      scene_yaxis_visible=False, 
                      scene_zaxis_visible=False)


    def rotate_z(x, y, z, theta):
        w = x+1j*y
        return np.real(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w), z

    # rot_speed = 20
    def make_frame(t):
        theta = t / 20 * 2 * np.pi
        xe, ye, ze = rotate_z(x_eye, y_eye, z_eye, -theta)
        fig.update_layout(scene_camera_eye=dict(x=xe, y=ye, z=ze))  #These are the updates that usually are performed within Plotly go.Frame definition
        return plotly_fig2array(fig)

    animation = mpy.VideoClip(make_frame, duration=5)
    animation.write_gif(outDir + imageName + '_' + gene_name + '.gif', fps=4)
